In [21]:
import random
import time
import plotly.express as px
import pandas as pd

In [22]:
class Player:
    def __init__(self, strategy):
        self.strategy = strategy
        self.score = 0
        self.last_opponent_move = None
        self.grudger_triggered = False
        self.pavlov_last_outcome = None
        self.detective_moves = ["cooperate", "backstab", "cooperate", "cooperate"]
        self.detective_index = 0
    
    def make_move(self):
        if self.strategy == "always_cooperate":
            return "cooperate"
        elif self.strategy == "always_backstab":
            return "backstab"
        elif self.strategy == "random":
            return random.choice(["cooperate", "backstab"])
        elif self.strategy == "tit_for_tat":
            if self.last_opponent_move is None:
                return "cooperate"
            else:
                return self.last_opponent_move
        elif self.strategy == "grudger":
            if self.grudger_triggered:
                return "backstab"
            else:
                return "cooperate"
        elif self.strategy == "pavlov":
            if self.pavlov_last_outcome is None or self.pavlov_last_outcome in ["both_cooperate", "both_backstab"]:
                return "cooperate"
            else:
                return "backstab"
        elif self.strategy == "randomly_defective":
            return "cooperate" if random.random() < 0.9 else "backstab"
        elif self.strategy == "detective":
            move = self.detective_moves[self.detective_index]
            self.detective_index = (self.detective_index + 1) % len(self.detective_moves)
            return move
        elif self.strategy == "forgiving_tit_for_tat":
            if self.last_opponent_move is None:
                return "cooperate"
            elif self.last_opponent_move == "backstab" and random.random() < 0.1:
                return "cooperate"
            else:
                return self.last_opponent_move
        else:
            raise ValueError("Unknown strategy")
    
    def update_score(self, points):
        self.score += points
    
    def update_last_opponent_move(self, move):
        self.last_opponent_move = move
        if self.strategy == "grudger" and move == "backstab":
            self.grudger_triggered = True
        if self.strategy == "pavlov":
            if self.last_opponent_move == "cooperate" and move == "cooperate":
                self.pavlov_last_outcome = "both_cooperate"
            elif self.last_opponent_move == "backstab" and move == "backstab":
                self.pavlov_last_outcome = "both_backstab"
            elif self.last_opponent_move == "cooperate" and move == "backstab":
                self.pavlov_last_outcome = "coop_backstab"
            elif self.last_opponent_move == "backstab" and move == "cooperate":
                self.pavlov_last_outcome = "backstab_coop"


In [23]:
def play_round(player1, player2):
    move1 = player1.make_move()
    move2 = player2.make_move()

    if move1 == "cooperate" and move2 == "cooperate":
        player1.update_score(3)
        player2.update_score(3)
    elif move1 == "backstab" and move2 == "backstab":
        player1.update_score(1)
        player2.update_score(1)
    elif move1 == "cooperate" and move2 == "backstab":
        player1.update_score(0)
        player2.update_score(4)
    elif move1 == "backstab" and move2 == "cooperate":
        player1.update_score(4)
        player2.update_score(0)

    player1.update_last_opponent_move(move2)
    player2.update_last_opponent_move(move1)

    return move1, move2


In [24]:
def print_colored(text, color_code):
    print(f"\033[{color_code}m{text}\033[0m", end='')

def simulate_game(player1, player2, rounds):
    print(f"\nMatch between {player1.strategy} and {player2.strategy}")
    print(f"{'Round':<6} {'Player 1':<12} {'Player 2':<12} {'Score 1':<8} {'Score 2':<8}")
    
    scores_per_round = {player1.strategy: [], player2.strategy: []}
    cumulative_score1 = 0
    cumulative_score2 = 0
    
    for round_num in range(1, rounds + 1):
        move1, move2 = play_round(player1, player2)
        
        cumulative_score1 += player1.score
        cumulative_score2 += player2.score
        scores_per_round[player1.strategy].append(cumulative_score1)
        scores_per_round[player2.strategy].append(cumulative_score2)
        
        move1_display = ("C" if move1 == "cooperate" else "B")
        move2_display = ("C" if move2 == "cooperate" else "B")
        
        move1_color = 42 if move1 == "cooperate" else 41 
        move2_color = 42 if move2 == "cooperate" else 41
        
        print(f"{round_num:<6} ", end='')
        print_colored(f"{move1_display:<12}", move1_color)
        print_colored(f"{move2_display:<12}", move2_color)
        print(f"{player1.score:<8} {player2.score:<8}")
        
        #time.sleep(0.07) 

    print("\nResults:")
    print(f"Player 1 ({player1.strategy}) Score: {player1.score}")
    print(f"Player 2 ({player2.strategy}) Score: {player2.score}")
    return scores_per_round

In [25]:
def run_multiple_matches(player_strategies, rounds):
    scores = {strategy: 0 for strategy in player_strategies}
    all_scores_per_round = {strategy: [] for strategy in player_strategies}

    for i in range(len(player_strategies)):
        for j in range(len(player_strategies)):
            if i != j:
                player1 = Player(strategy=player_strategies[i])
                player2 = Player(strategy=player_strategies[j])
                scores_per_round = simulate_game(player1, player2, rounds)
                for strategy in scores_per_round:
                    all_scores_per_round[strategy].extend(scores_per_round[strategy])
                scores[player1.strategy] += player1.score
                scores[player2.strategy] += player2.score
    
    sorted_scores = sorted(scores.items(), key=lambda x: x[1], reverse=True)
    
    
    print("\nFinal Results:")
    print(f"{'Strategy':<20} {'Cumulative Points':<20}")
    for strategy, score in sorted_scores:
        print(f"{strategy:<20} {score:<20}")

        
    scores_df = pd.DataFrame(list(scores.items()), columns=['Strategy', 'Cumulative Points'])
    fig = px.bar(scores_df, x='Strategy', y='Cumulative Points', title='Cumulative Points by Strategy')
    fig.show()

    
    rounds_df = pd.DataFrame(all_scores_per_round)
    rounds_df.index.name = 'Round'
    rounds_df.reset_index(inplace=True)
    
   
    rounds_df_melted = rounds_df.melt(id_vars=['Round'], var_name='Strategy', value_name='Cumulative Score')
    
    
    line_fig = px.line(rounds_df_melted, x='Round', y='Cumulative Score', color='Strategy', title='Cumulative Scores per Round by Strategy')
    line_fig.show()


In [26]:
def run_grouped_population(rounds=100):
    strategy_population = [
        ("always_cooperate", 10),
        ("always_backstab", 10),
        ("random", 10),
        ("tit_for_tat", 10),
        ("grudger", 10),
        ("pavlov", 10),
        ("randomly_defective", 10),
        ("detective", 10),
        ("forgiving_tit_for_tat", 10)
    ]

   
    good_strategies = ["always_cooperate", "tit_for_tat", "grudger", "pavlov", "forgiving_tit_for_tat"]
    evil_strategies = ["always_backstab", "random", "randomly_defective", "detective"]
    
   
    good_players = []
    evil_players = []
    for strategy, num_players in strategy_population:
        for _ in range(num_players):
            if strategy in good_strategies:
                good_players.append(Player(strategy=strategy))
            elif strategy in evil_strategies:
                evil_players.append(Player(strategy=strategy))

   
    good_scores = {strategy: 0 for strategy, _ in strategy_population if strategy in good_strategies}
    evil_scores = {strategy: 0 for strategy, _ in strategy_population if strategy in evil_strategies}
    all_scores_per_round = {strategy: [] for strategy, _ in strategy_population}

    
    for _ in range(rounds):
        random.shuffle(good_players)
        for i in range(0, len(good_players), 2):
            if i + 1 < len(good_players):
                player1 = good_players[i]
                player2 = good_players[i + 1]
                scores_per_round = simulate_game(player1, player2, 1)
                for strategy in scores_per_round:
                    all_scores_per_round[strategy].extend(scores_per_round[strategy])
                good_scores[player1.strategy] += player1.score
                good_scores[player2.strategy] += player2.score
    
   
    for _ in range(rounds):
        random.shuffle(evil_players)
        for i in range(0, len(evil_players), 2):
            if i + 1 < len(evil_players):
                player1 = evil_players[i]
                player2 = evil_players[i + 1]
                scores_per_round = simulate_game(player1, player2, 1)
                for strategy in scores_per_round:
                    all_scores_per_round[strategy].extend(scores_per_round[strategy])
                evil_scores[player1.strategy] += player1.score
                evil_scores[player2.strategy] += player2.score
    
    
    good_scores_df = pd.DataFrame(list(good_scores.items()), columns=['Strategy', 'Cumulative Points'])
    evil_scores_df = pd.DataFrame(list(evil_scores.items()), columns=['Strategy', 'Cumulative Points'])
    good_fig = px.bar(good_scores_df, x='Strategy', y='Cumulative Points', title='Cumulative Points by Good Strategies')
    evil_fig = px.bar(evil_scores_df, x='Strategy', y='Cumulative Points', title='Cumulative Points by Evil Strategies')
    good_fig.show()
    evil_fig.show()

    
    rounds_df = pd.DataFrame(all_scores_per_round)
    rounds_df.index.name = 'Round'
    rounds_df.reset_index(inplace=True)
    
   
    rounds_df_melted = rounds_df.melt(id_vars=['Round'], var_name='Strategy', value_name='Cumulative Score')
    
    
    line_fig = px.line(rounds_df_melted, x='Round', y='Cumulative Score', color='Strategy', title='Cumulative Scores per Round by Strategy')
    line_fig.show()

In [27]:
def main():
    strategies = [
        "always_cooperate",
        "always_backstab",
        "random",
        "tit_for_tat",
        "grudger",
        "pavlov",
        "randomly_defective",
        "detective",
        "forgiving_tit_for_tat"
    ]
    rounds = 200
    run_multiple_matches(strategies, rounds)
    run_grouped_population(rounds)

if __name__ == "__main__":
    main()


Match between always_cooperate and always_backstab
Round  Player 1     Player 2     Score 1  Score 2 
1      C           B           0        4       
2      C           B           0        8       
3      C           B           0        12      
4      C           B           0        16      
5      C           B           0        20      
6      C           B           0        24      
7      C           B           0        28      
8      C           B           0        32      
9      C           B           0        36      
10     C           B           0        40      
11     C           B           0        44      
12     C           B           0        48      
13     C           B           0        52      
14     C           B           0        56      
15     C           B           0        60      
16     C           B           0        64      
17     C           B           0        68      
18     C           B           0        72      
19     C       


Match between tit_for_tat and tit_for_tat
Round  Player 1     Player 2     Score 1  Score 2 
1      C           C           3        3       

Results:
Player 1 (tit_for_tat) Score: 3
Player 2 (tit_for_tat) Score: 3

Match between tit_for_tat and forgiving_tit_for_tat
Round  Player 1     Player 2     Score 1  Score 2 
1      C           C           3        3       

Results:
Player 1 (tit_for_tat) Score: 3
Player 2 (forgiving_tit_for_tat) Score: 3

Match between grudger and always_cooperate
Round  Player 1     Player 2     Score 1  Score 2 
1      C           C           3        3       

Results:
Player 1 (grudger) Score: 3
Player 2 (always_cooperate) Score: 3

Match between grudger and grudger
Round  Player 1     Player 2     Score 1  Score 2 
1      C           C           3        3       

Results:
Player 1 (grudger) Score: 3
Player 2 (grudger) Score: 3

Match between tit_for_tat and tit_for_tat
Round  Player 1     Player 2     Score 1  Score 2 
1      C           C           3